In [1]:
import numpy as np
import pandas as pd
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.linear_model import LogisticRegression
from lightgbm import LGBMClassifier
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import VotingClassifier

import pandas as pd
import random
import os
import numpy as np

from sklearn.linear_model import LinearRegression
from sklearn.multioutput import MultiOutputRegressor

import xgboost as xgb
import random

C:\Users\user\anaconda3\lib\site-packages\numpy\_distributor_init.py:30: UserWarning: loaded more than 1 DLL from .libs:
C:\Users\user\anaconda3\lib\site-packages\numpy\.libs\libopenblas.FB5AE2TYXYH2IJRDKGDGQ3XBKLKTF43H.gfortran-win_amd64.dll
C:\Users\user\anaconda3\lib\site-packages\numpy\.libs\libopenblas.WCDJNK7YVMPZQ2ME2ZZHJJRJ3JIKNDB7.gfortran-win_amd64.dll
  warnings.warn("loaded more than 1 DLL from .libs:"
<frozen importlib._bootstrap>:219: RuntimeWarning: scipy._lib.messagestream.MessageStream size changed, may indicate binary incompatibility. Expected 56 from C header, got 64 from PyObject
C:\Users\user\anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)
C:\Users\user\anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.Fl

In [2]:
import jinja2
import datetime as dt
import matplotlib.pyplot as plt
from tqdm import tqdm
import gc
import random
import lightgbm as lgb
import re
from sklearn.metrics import *
from sklearn.model_selection import KFold
import warnings
warnings.filterwarnings(action='ignore')
from supervised.automl import AutoML
# from pycaret.classification import * 

In [51]:
train = pd.read_excel('./dataset_train.xlsx',engine ='openpyxl')
# test = label_encoder(test, make_label_map(test))
train = train.drop('number', axis=1)
train.head()

sex  age Q1  Q2  Q3  Q4 Q5 D1  D2 D3  ...  Esomeprazole 20 mg  \
0   F   67  6   2   2   2  5  7  11  5  ...                   2   
1   F   70  6   2   2   2  2  7  11  1  ...                   2   
2   F   72  5   2   2   2  2  7  11  5  ...                   2   
3   M   73  5   2   2   2  2  7  11  1  ...                   2   
4   M   79  5   2   2   2  6  6   7  5  ...                   1   

   Esomeprazole 40 mg  Ilaprazole 10 mg(놀텍)  Ilaprazole 20 mg  약물1_None  \
0                   2                     2                 2         1   
1                   2                     2                 2         1   
2                   2                     2                 2         1   
3                   2                     2                 2         1   
4                   2                     2                 2         2   

   Ranitidine(알비스)  Famotidine  Lafutidine(스토가)  Mucosta  약물2_None  
0                2           2                2        2         1  
1                1           2                2        2         2  
2                2           2                2        2         1  
3                1           2                2        2         2  
4                2           2                2        2         1  

[5 rows x 68 columns]

In [52]:
inter_valid = pd.read_excel('./dataset_incheon_test.xlsx',engine ='openpyxl')
# test = label_encoder(test, make_label_map(test))
inter_valid = inter_valid.drop('number', axis=1)
inter_valid.head()

sex  age Q1  Q2  Q3  Q4   Q5  D1  D2  D3  ...  Esomeprazole 40 mg  \
0   M   82  4   2   2   2    2   3  11   1  ...                   2   
1   F   84  3   2   2   2  2,3   3  11   5  ...                   2   
2   F   82  5   2   2   2    6  10   4   5  ...                   2   
3   M   57  4   2   2   2    1  11   7   5  ...                   2   
4   F   68  2   2   2   2  1,2  10  11   3  ...                   2   

   Ilaprazole 10 mg(놀텍)  Ilaprazole 20 mg  약물1_None  Ranitidine(알비스)  \
0                     2                 2         1                1   
1                     2                 2         1                2   
2                     2                 2         2                2   
3                     2                 2         2                2   
4                     2                 2         1                2   

   Famotidine  Lafutidine(스토가)  Mucosta  약물2_None  total_med  
0           2                2        2         2          2  
1           2                2        2         1          1  
2           2                2        2         1          2  
3           2                2        2         1          2  
4           2                1        2         2          3  

[5 rows x 69 columns]

In [53]:
exter_valid = pd.read_excel('./external_valid.xlsx',engine ='openpyxl')
# test = label_encoder(test, make_label_map(test))
exter_valid = exter_valid.drop('number', axis=1)
exter_valid.head()

sex  age     Q1  Q2  Q3  Q4 Q5  D1  D2 D3  ...  Esomeprazole 40 mg  \
0   F   80      4   2   2   2  2   7  11  5  ...                   2   
1   F   77      4   2   2   2  1   4  11  4  ...                   2   
2   M   76  2,4,5   2   2   2  1   4  11  1  ...                   2   
3   F   64      4   2   2   2  1   4  11  1  ...                   2   
4   F   59    5,6   2   2   2  6   8  11  4  ...                   2   

   Ilaprazole 10 mg(놀텍)  Ilaprazole 20 mg  약물1_None  Ranitidine(알비스)  \
0                     2                 2         1                2   
1                     2                 2         1                2   
2                     2                 2         1                1   
3                     2                 2         1                1   
4                     2                 2         1                2   

   Famotidine  Lafutidine(스토가)  Mucosta  약물2_None  total_med  
0           2                2        2         1          2  
1           2                2        1         2          2  
2           2                2        2         2          2  
3           2                2        2         2          2  
4           2                2        1         2          2  

[5 rows x 69 columns]

In [54]:
def check_missing_col(dataframe):
    missing_col = []
    for col in dataframe.columns:
        missing_values = sum(dataframe[col].isna())
        is_missing = True if missing_values >= 1 else False
        if is_missing:
            print(f'결측치가 있는 컬럼은: {col} 입니다')
            print(f'해당 컬럼에 총 {missing_values} 개의 결측치가 존재합니다.')
            missing_col.append([col, dataframe[col].dtype])
    if missing_col == []:
        print('결측치가 존재하지 않습니다')
    return missing_col

missing_col = check_missing_col(train)

# missing_col_test = check_missing_col(test)


결측치가 존재하지 않습니다


In [55]:
# 결측치를 처리하는 함수를 작성합니다.
def handle_na(data, missing_col):
    temp = data.copy()
    for col, dtype in missing_col:
        if dtype == 'O':
            # 범주형 feature가 결측치인 경우 해당 행들을 삭제해 주었습니다.
            temp = temp.dropna(subset=[col])
    return temp

train = handle_na(train, missing_col)

# 결측치 처리가 잘 되었는지 확인해 줍니다.
missing_col = check_missing_col(train) 

결측치가 존재하지 않습니다


In [56]:
from sklearn.model_selection import train_test_split

train = train.drop(['Mortality', 'Q1', 'Q5', 'D1','D2','D3','EGD'], axis = 1).copy() #필요없는 id열 삭제
# train = train.drop(['Mortality','EGD'], axis = 1).copy() #필요없는 id열 삭제
# train = train.drop('modified_GIB', axis = 1).copy() #필요없는 id열 삭제
# train = train.drop('GIB', axis = 1).copy() #필요없는 id열 삭제
train = train.drop('Intracranial hemorrhage', axis = 1).copy() #필요없는 id열 삭제
# train = train.drop('D6', axis = 1).copy() #필요없는 id열 삭제
train = train.drop('Transfusion', axis = 1).copy() #필요없는 id열 삭제


inter_valid = inter_valid.drop(['Mortality', 'Q1', 'Q5', 'D1','D2','D3','EGD'], axis = 1).copy() #필요없는 id열 삭제
# inter_valid = inter_valid.drop(['Mortality', 'EGD'], axis = 1).copy() #필요없는 id열 삭제
inter_valid = inter_valid.drop('Intracranial hemorrhage', axis = 1).copy() #필요없는 id열 삭제
inter_valid = inter_valid.drop('Transfusion', axis = 1).copy() #필요없는 id열 삭제

exter_valid = exter_valid.drop(['Mortality', 'Q1', 'Q5', 'D1','D2','D3','EGD'], axis = 1).copy() #필요없는 id열 삭제
# exter_valid = exter_valid.drop(['Mortality','EGD'], axis = 1).copy() #필요없는 id열 삭제
exter_valid = exter_valid.drop('Intracranial hemorrhage', axis = 1).copy() #필요없는 id열 삭제
exter_valid = exter_valid.drop('Transfusion', axis = 1).copy() #필요없는 id열 삭제


In [57]:
train

sex  age  Q2  Q3  Q4  D4  D5  D6  D7  D8  ...  Esomeprazole 20 mg  \
0      F   67   2   2   2   2   2   2   2   2  ...                   2   
1      F   70   2   2   2   2   2   2   2   2  ...                   2   
2      F   72   2   2   2   2   2   2   2   2  ...                   2   
3      M   73   2   2   2   2   2   2   2   2  ...                   2   
4      M   79   2   2   2   2   2   2   2   2  ...                   1   
...   ..  ...  ..  ..  ..  ..  ..  ..  ..  ..  ...                 ...   
3977   F   78   2   2   2   2   2   2   2   2  ...                   2   
3978   F   80   2   2   2   2   2   2   2   2  ...                   2   
3979   F   83   2   2   2   2   2   2   2   1  ...                   2   
3980   F   81   2   2   2   2   2   2   2   2  ...                   2   
3981   F   64   1   1   1   2   2   2   2   2  ...                   2   

      Esomeprazole 40 mg  Ilaprazole 10 mg(놀텍)  Ilaprazole 20 mg  약물1_None  \
0                      2                     2                 2         1   
1                      2                     2                 2         1   
2                      2                     2                 2         1   
3                      2                     2                 2         1   
4                      2                     2                 2         2   
...                  ...                   ...               ...       ...   
3977                   2                     2                 2         1   
3978                   2                     2                 2         1   
3979                   2                     2                 2         2   
3980                   2                     2                 2         1   
3981                   2                     2                 2         2   

      Ranitidine(알비스)  Famotidine  Lafutidine(스토가)  Mucosta  약물2_None  
0                   2           2                2        2         1  
1                   1           2                2        2         2  
2                   2           2                2        2         1  
3                   1           2                2        2         2  
4                   2           2                2        2         1  
...               ...         ...              ...      ...       ...  
3977                2           2                1        2         2  
3978                2           2                2        2         1  
3979                2           2                2        2         1  
3980                2           2                2        2         1  
3981                2           2                2        2         1  

[3982 rows x 59 columns]

In [58]:
train['L4']

0       1.10
1       0.97
2       0.94
3       1.50
4       1.45
        ... 
3977    1.27
3978    1.00
3979    0.99
3980    0.99
3981    1.00
Name: L4, Length: 3982, dtype: float64

In [59]:
train.GIB = train.GIB.replace({1:1, 2:0})
inter_valid.GIB = inter_valid.GIB.replace({1:1, 2:0})
exter_valid.GIB = exter_valid.GIB.replace({1:1, 2:0})

In [60]:

from sklearn.utils.class_weight import compute_sample_weight


automl = AutoML(mode="Optuna", ml_task="binary_classification"
    , eval_metric='auc',
    total_time_limit = 14*3600,
    stack_models = 'auto',
    random_state=42, results_path="optuna")

X_train = train.drop('GIB',axis=1)
y_train = train['GIB'].astype("int64")

# weights = compute_sample_weight(class_weight="balanced", y=y_train)

automl.fit(X_train, y_train)

AutoML directory: optuna
Expected computing time:
Time for tuning with Optuna: len(algorithms) * optuna_time_budget = 21600 seconds
There is no time limit for ML model training after Optuna tuning (total_time_limit parameter is ignored).
The task is binary_classification with evaluation metric auc
AutoML will use algorithms: ['Random Forest', 'Extra Trees', 'LightGBM', 'Xgboost', 'CatBoost', 'Neural Network']
AutoML will stack models
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble', 'stack', 'ensemble_stacked']
Skip simple_algorithms because no parameters were generated.
* Step default_algorithms will try to check up to 6 models


[I 2022-12-26 19:49:54,220] A new study created in memory with name: no-name-46e9c785-1737-4c14-80d8-090d1b0b47ae
[I 2022-12-26 19:49:54,314] Trial 0 finished with value: 0.8358096468561586 and parameters: {'learning_rate': 0.025, 'num_leaves': 321, 'lambda_l1': 2.5348407664333426e-07, 'lambda_l2': 3.3323645788192616e-08, 'feature_fraction': 0.9063233107042159, 'bagging_fraction': 0.7207805142313962, 'bagging_freq': 5, 'min_data_in_leaf': 3, 'extra_trees': True}. Best is trial 0 with value: 0.8358096468561586.


Optuna optimizes LightGBM with time budget 3600 seconds eval_metric auc (maximize)


[I 2022-12-26 19:49:54,392] Trial 1 finished with value: 0.8154608096468562 and parameters: {'learning_rate': 0.1, 'num_leaves': 1076, 'lambda_l1': 7.71800699380605e-05, 'lambda_l2': 4.17890272377219e-06, 'feature_fraction': 0.7282970324241945, 'bagging_fraction': 0.3976457038513679, 'bagging_freq': 3, 'min_data_in_leaf': 37, 'extra_trees': False}. Best is trial 0 with value: 0.8358096468561586.
[I 2022-12-26 19:49:54,704] Trial 2 finished with value: 0.8128768303186908 and parameters: {'learning_rate': 0.05, 'num_leaves': 1245, 'lambda_l1': 3.425445902633376e-07, 'lambda_l2': 3.850031979199519e-08, 'feature_fraction': 0.9642198855661885, 'bagging_fraction': 0.9759424328085118, 'bagging_freq': 6, 'min_data_in_leaf': 31, 'extra_trees': False}. Best is trial 0 with value: 0.8358096468561586.
[I 2022-12-26 19:49:54,767] Trial 3 finished with value: 0.8083548664944012 and parameters: {'learning_rate': 0.05, 'num_leaves': 1863, 'lambda_l1': 2.133142332373004e-06, 'lambda_l2': 0.009176996354

[I 2022-12-26 19:49:56,096] Trial 21 finished with value: 0.8049095607235142 and parameters: {'learning_rate': 0.1, 'num_leaves': 534, 'lambda_l1': 0.006972602332282105, 'lambda_l2': 0.24316267266114514, 'feature_fraction': 0.737986251196221, 'bagging_fraction': 0.7974327734846708, 'bagging_freq': 2, 'min_data_in_leaf': 29, 'extra_trees': False}. Best is trial 18 with value: 0.8940568475452196.
[I 2022-12-26 19:49:56,236] Trial 22 finished with value: 0.7993109388458227 and parameters: {'learning_rate': 0.1, 'num_leaves': 379, 'lambda_l1': 0.002280790450560079, 'lambda_l2': 0.0015523143947329448, 'feature_fraction': 0.9213057101198792, 'bagging_fraction': 0.9027588810226764, 'bagging_freq': 4, 'min_data_in_leaf': 13, 'extra_trees': False}. Best is trial 18 with value: 0.8940568475452196.
[I 2022-12-26 19:49:56,298] Trial 23 finished with value: 0.8337639965546942 and parameters: {'learning_rate': 0.025, 'num_leaves': 170, 'lambda_l1': 0.0004717738301517202, 'lambda_l2': 0.0291371186682

...

[I 2022-12-27 01:34:08,515] Trial 2134 finished with value: 0.8294573643410853 and parameters: {'criterion': 'entropy', 'max_depth': 3, 'min_samples_split': 63, 'min_samples_leaf': 13, 'max_features': 0.9507374850338812}. Best is trial 1411 with value: 0.8593884582256675.
[I 2022-12-27 01:34:10,001] Trial 2135 finished with value: 0.835055986218777 and parameters: {'criterion': 'entropy', 'max_depth': 4, 'min_samples_split': 12, 'min_samples_leaf': 17, 'max_features': 0.9817248660239312}. Best is trial 1411 with value: 0.8593884582256675.
[I 2022-12-27 01:34:11,485] Trial 2136 finished with value: 0.8385012919896642 and parameters: {'criterion': 'entropy', 'max_depth': 4, 'min_samples_split': 15, 'min_samples_leaf': 14, 'max_features': 0.9832833057903049}. Best is trial 1411 with value: 0.8593884582256675.
[I 2022-12-27 01:34:12,812] Trial 2137 finished with value: 0.8044788975021534 and parameters: {'criterion': 'gini', 'max_depth': 2, 'min_samples_split': 18, 'min_samples_leaf': 12, 

[I 2022-12-27 01:34:53,876] Trial 2163 finished with value: 0.8369939707149009 and parameters: {'criterion': 'entropy', 'max_depth': 5, 'min_samples_split': 9, 'min_samples_leaf': 18, 'max_features': 0.9528718253776438}. Best is trial 1411 with value: 0.8593884582256675.
[I 2022-12-27 01:34:55,267] Trial 2164 finished with value: 0.835055986218777 and parameters: {'criterion': 'entropy', 'max_depth': 3, 'min_samples_split': 10, 'min_samples_leaf': 15, 'max_features': 0.8785673014742775}. Best is trial 1411 with value: 0.8593884582256675.
[I 2022-12-27 01:34:56,829] Trial 2165 finished with value: 0.8531438415159345 and parameters: {'criterion': 'entropy', 'max_depth': 5, 'min_samples_split': 17, 'min_samples_leaf': 10, 'max_features': 0.9382275056431923}. Best is trial 1411 with value: 0.8593884582256675.
[I 2022-12-27 01:34:58,172] Trial 2166 finished with value: 0.8298880275624462 and parameters: {'criterion': 'entropy', 'max_depth': 2, 'min_samples_split': 11, 'min_samples_leaf': 13

[I 2022-12-27 01:35:39,004] Trial 2192 finished with value: 0.8092161929371231 and parameters: {'criterion': 'gini', 'max_depth': 6, 'min_samples_split': 15, 'min_samples_leaf': 12, 'max_features': 0.4138504295302685}. Best is trial 1411 with value: 0.8593884582256675.
[I 2022-12-27 01:35:40,723] Trial 2193 finished with value: 0.8501291989664084 and parameters: {'criterion': 'entropy', 'max_depth': 6, 'min_samples_split': 13, 'min_samples_leaf': 10, 'max_features': 0.9018015942868954}. Best is trial 1411 with value: 0.8593884582256675.
[I 2022-12-27 01:35:42,347] Trial 2194 finished with value: 0.83656330749354 and parameters: {'criterion': 'entropy', 'max_depth': 4, 'min_samples_split': 19, 'min_samples_leaf': 15, 'max_features': 0.9253063195752311}. Best is trial 1411 with value: 0.8593884582256675.
[I 2022-12-27 01:35:43,738] Trial 2195 finished with value: 0.8322566752799311 and parameters: {'criterion': 'entropy', 'max_depth': 3, 'min_samples_split': 12, 'min_samples_leaf': 13, '

6_Optuna_ExtraTrees auc 0.6945 trained in 8.8 seconds
* Step ensemble will try to check up to 1 model
Ensemble auc 0.74599 trained in 0.92 seconds
* Step stack will try to check up to 6 models
5_Optuna_RandomForest_Stacked auc 0.671353 trained in 10.17 seconds
6_Optuna_ExtraTrees_Stacked auc 0.73107 trained in 9.41 seconds
1_Optuna_LightGBM_Stacked auc 0.662525 trained in 5.7 seconds
4_Optuna_NeuralNetwork_Stacked auc 0.63808 trained in 12.36 seconds
3_Optuna_CatBoost_Stacked auc 0.601135 trained in 5.53 seconds
2_Optuna_Xgboost_Stacked auc 0.532731 trained in 5.46 seconds
* Step ensemble_stacked will try to check up to 1 model
Ensemble_Stacked auc 0.750514 trained in 1.27 seconds
AutoML fit time: 20991.29 seconds
AutoML best model: Ensemble_Stacked


AutoML(eval_metric='auc', ml_task='binary_classification', mode='Optuna',
       random_state=42, results_path='optuna', total_time_limit=50400)

In [72]:
X_inter = inter_valid.drop('GIB',axis=1)
y_inter = inter_valid['GIB'].astype("int64")

y_pred_prob = automl.predict_proba(X_inter)
print(f"AUROC: {roc_auc_score(y_inter, automl.predict(X_inter)):.2f}%")

AUROC: 0.50%


In [71]:
len(automl.predict(X_inter))

451

In [74]:
y_inter

0      0
1      0
2      0
3      0
4      0
      ..
446    0
447    0
448    0
449    0
450    0
Name: GIB, Length: 451, dtype: int64

In [75]:
X_exter = exter_valid.drop('GIB',axis=1)
y_exter = exter_valid['GIB'].astype("int64")

y_pred_prob = automl.predict_proba(X_exter)
print(f"AUROC: {roc_auc_score(y_exter, automl.predict(X_exter)):.2f}%")

AUROC: 0.50%
